# LAB 05: Exploring issues were behind the UK's vote to leave the EU

The EU referendum in which a majority of voters voted to leave the EU was just under a decade ago. Here, we consider how we might use visual analytics to explore some of the issues behind the vote.

When considering these data, think about the types of analytical task (from Lecture 2), what kinds of numerical analysis and what visualisation designs would help you.

 - Describe: Distribution of variables (e.g. histograms, box plots and maps)
 - Locate: Which records have values that are high and low? (e.g. sorted lists, maps)
 - Compare: How to data compare to each other (e.g. sorted lists and maps, perhaps using difference and perhaps using a diverging axis or colour scale)
 - Relate: How do variables relate (e.g. correlation matrices, scatterplots)

You will likely want to do all these. **Describe** and **locate** are very simple. When doing Visual Analytics, so also find some **compare** and **relate** tasks.


## Loading geographical boundaries

The data are at Local Authority level, so we will load boundary data for these.

[Shapefiles](https://en.wikipedia.org/wiki/Shapefile) are a GIS file format for providing geographical boundaries. We provide geographical boundaries for Local Authorities and also provide a hexagonal cartogram version.

If you don't have the Shapefile data, they are [here](https://staff.city.ac.uk/moodle/2023-2024/inm433/session05/shapefiles.zip).

This is done using the `geopandas` library enables dataframe columns to contain spatial data. Look at the data that result and you'll see a "geometry" column.

We're also manually assigning a couple of regions (see https://findthatpostcode.uk/areas/E06000052.html and https://findthatpostcode.uk/areas/E41000052.html; this is allocating the Isles of Scilly to Cornwall).

In [1]:
import os
os.environ['USE_PYGEOS'] = '0'
import geopandas as gpd

# boundaries
la_boundaries = gpd.read_file("shapefiles/boundaries_gb.shp")
la_boundaries.loc[la_boundaries["geo_code"]=="E41000052",'geo_code'] = "E06000052"
la_boundaries.loc[la_boundaries["geo_code"]=="E41000324",'geo_code'] = "E09000033"
#calculate the area of each local authority
la_boundaries["shapeArea"]=la_boundaries["geometry"].area

#cartograms
la_carto = gpd.read_file("shapefiles/GB_Hex_Cartogram_LAs.shp")

In [2]:
la_boundaries

geo_labelw         geo_label   geo_code          AREA      PERIMETER  \
0          NaN    South Ayrshire  S12000028  1.222498e+09  271424.465207   
1          NaN   Huntingdonshire  E07000011  9.129696e+08  207912.519811   
2          NaN        Tewkesbury  E07000083  4.146167e+08  183303.084764   
3          NaN   West Lancashire  E07000127  3.473296e+08  111348.525350   
4          NaN        Darlington  E06000005  1.976383e+08   99068.282044   
..         ...               ...        ...           ...            ...   
373        NaN       East Dorset  E07000049  3.542086e+08  127976.707281   
374        NaN          Torridge  E07000046  9.851546e+08  247641.630690   
375        NaN  Stockton-on-Tees  E06000004  2.040348e+08  127367.554864   
376        NaN   Perth & Kinross  S12000024  5.287716e+09  750874.398299   
377        NaN             Selby  E07000169  5.999190e+08  218957.154698   

                                              geometry     shapeArea  
0    POLYGON ((243296.000 588978.200, 242159.500 58...  1.220472e+09  
1    POLYGON ((507472.314 299057.906, 511995.531 29...  9.127571e+08  
2    POLYGON ((381509.283 230085.397, 385473.094 23...  4.164018e+08  
3    POLYGON ((337708.438 420693.956, 337713.301 42...  3.580191e+08  
4    POLYGON ((419709.307 515678.312, 418911.500 51...  2.007936e+08  
..                                                 ...           ...  
373  POLYGON ((395369.690 116934.897, 397676.807 11...  3.595242e+08  
374  POLYGON ((245929.902 126948.298, 257377.496 12...  9.852863e+08  
375  MULTIPOLYGON (((436387.995 522354.195, 440052....  1.935023e+08  
376  POLYGON ((321168.000 718296.600, 319686.200 71...  5.373173e+09  
377  MULTIPOLYGON (((452922.656 447657.846, 455350....  6.024568e+08  

[378 rows x 7 columns]

## Referendum data

We'll now import the EU referendum data. This contains counts by **Local Authority**.

If you don't have the data, they are [here](https://staff.city.ac.uk/moodle/2023-2024/inm433/session05/data.zip).

In [3]:
import os
os.environ['USE_PYGEOS'] = '0'
import pandas as pd

referendum_data = pd.read_csv("data/referendum_data.csv")

In [4]:
referendum_data

Region_Code                    Region  Area_Code             Area  \
0     E12000006                      East  E06000031     Peterborough   
1     E12000006                      East  E06000032            Luton   
2     E12000006                      East  E06000033  Southend-on-Sea   
3     E12000006                      East  E06000034         Thurrock   
4     E12000006                      East  E06000055          Bedford   
..          ...                       ...        ...              ...   
373   E12000003  Yorkshire and The Humber  E08000032         Bradford   
374   E12000003  Yorkshire and The Humber  E08000033       Calderdale   
375   E12000003  Yorkshire and The Humber  E08000034         Kirklees   
376   E12000003  Yorkshire and The Humber  E08000035            Leeds   
377   E12000003  Yorkshire and The Humber  E08000036        Wakefield   

     Electorate  Turnout  Valid_Votes   Leave  
0        120892   0.7235        87392  0.6089  
1        127612   0.6631        84481  0.5655  
2        128856   0.7290        93870  0.5808  
3        109897   0.7275        79916  0.7228  
4        119530   0.7206        86066  0.5178  
..          ...      ...          ...     ...  
373      342817   0.6672       228488  0.5423  
374      149195   0.7105       105925  0.5568  
375      307081   0.7080       217240  0.5467  
376      543033   0.7139       387337  0.4969  
377      246096   0.7117       175042  0.6636  

[378 rows x 8 columns]

Let's add the geometry to the referendum_data, using Panda's `merge()` method.

In [5]:
#Based on conventioned map boundaries
referendum_data = pd.merge(la_boundaries[["geo_code","geometry","shapeArea"]],referendum_data,left_on='geo_code', right_on='Area_Code', how='inner')
referendum_data

geo_code                                           geometry  \
0    S12000028  POLYGON ((243296.000 588978.200, 242159.500 58...   
1    E07000011  POLYGON ((507472.314 299057.906, 511995.531 29...   
2    E07000083  POLYGON ((381509.283 230085.397, 385473.094 23...   
3    E07000127  POLYGON ((337708.438 420693.956, 337713.301 42...   
4    E06000005  POLYGON ((419709.307 515678.312, 418911.500 51...   
..         ...                                                ...   
373  E07000049  POLYGON ((395369.690 116934.897, 397676.807 11...   
374  E07000046  POLYGON ((245929.902 126948.298, 257377.496 12...   
375  E06000004  MULTIPOLYGON (((436387.995 522354.195, 440052....   
376  S12000024  POLYGON ((321168.000 718296.600, 319686.200 71...   
377  E07000169  MULTIPOLYGON (((452922.656 447657.846, 455350....   

        shapeArea Region_Code                    Region  Area_Code  \
0    1.220472e+09   S92000003                  Scotland  S12000028   
1    9.127571e+08   E12000006                      East  E07000011   
2    4.164018e+08   E12000009                South West  E07000083   
3    3.580191e+08   E12000002                North West  E07000127   
4    2.007936e+08   E12000001                North East  E06000005   
..            ...         ...                       ...        ...   
373  3.595242e+08   E12000009                South West  E07000049   
374  9.852863e+08   E12000009                South West  E07000046   
375  1.935023e+08   E12000001                North East  E06000004   
376  5.373173e+09   S92000003                  Scotland  S12000024   
377  6.024568e+08   E12000003  Yorkshire and The Humber  E07000169   

                  Area  Electorate  Turnout  Valid_Votes   Leave  
0       South Ayrshire       88116   0.6984        61506  0.4104  
1      Huntingdonshire      128486   0.7782        99927  0.5424  
2           Tewkesbury       67831   0.7915        53652  0.5325  
3      West Lancashire       85834   0.7447        63869  0.5531  
4           Darlington       77662   0.7107        55166  0.5618  
..                 ...         ...      ...          ...     ...  
373        East Dorset       71966   0.8133        58488  0.5762  
374           Torridge       52881   0.7841        41429  0.6083  
375   Stockton-on-Tees      141486   0.7100       100415  0.6173  
376  Perth and Kinross      110224   0.7375        81255  0.3891  
377              Selby       65278   0.7910        51603  0.5917  

[378 rows x 11 columns]

Also useful to calculate a measure that's greater than zero for leave and less that zero for remain.

In [6]:
referendum_data["leave_remain"] = referendum_data["Leave"]-0.5

### Task 1: Come up with some questions (analytical tasks) on the referendum data. 

These may include:
 - What proportion of areas voted leave? (Although the referendum results were based on proportional representation, were the more or fewer areas that voted one way or the other?)
 - How much consensus within areas related to whether they voted to leave/remain?
 - Is there a relationship between voter turnout and the leave-remain vote? (Voter turnout might indicate vote apathy/engagement)
 - Are there geographical patterns in leave/remain areas or turnout? (Why would there be voting differences?)

Can your interpretations help you understand some of the issues behind the vote decisions?

**Use whichever software and/or libraries you like!** You might also like to try plotting cartogram maps (using the `la_carto` dataframe).

YOUR ANSWERS HERE

### Examples for Task 1

Here are some examples that might help you. Use whichever software and/or libraries you like!

In [7]:
import altair as alt

alt.Chart(referendum_data).mark_bar(strokeWidth=0).encode(
    x='leave_remain:Q',
    y=alt.Y('Area:N',sort='-x',axis=None),
    color=alt.Color('leave_remain:Q', scale=alt.Scale(scheme='brownbluegreen',domain=([-0.4,0.4]))),
    tooltip=['Area:N','leave_remain:Q','Region:N']
).properties(
    projection={'type': 'identity','reflectY': True},
    width=200,
    height=300
)

alt.Chart(...)

In [8]:
alt.Chart(referendum_data).mark_circle(strokeWidth=0,opacity=0.3).encode(
    x='Leave:Q',
    y='Turnout:Q',
    color='Region',
    tooltip=['Area:N']
).properties(
    width=200,
    height=200
)

alt.Chart(...)

In [9]:
alt.Chart(referendum_data).mark_geoshape(strokeWidth=1,stroke='lightgray',strokeOpacity=0.2
).encode(
    color=alt.Color('leave_remain:Q', scale=alt.Scale(scheme='brownbluegreen',domain=([-0.4,0.4]))),
    tooltip=['Area:N','leave_remain:Q','Region:N']
).properties(
 projection={'type': 'identity','reflectY': True},
    width=200,
    height=300
)

alt.Chart(...)

## Can socioeconomic variables help explain the voting behaviour?


In the lecture, we discussed possible datasets we could use to investigate these issues. We don't have individual data, but we know the area where voters live. So we can use census data which provides aggregate sociodemographics statistics by Output Area (OA) to help characterise them.

Output Area (OA) and Local Authority (LA) are two different UK spatial units. The referendum results are by Local Authority (LA) and the census is available at the much finer Output Area (OA) level. OAs nest inside LAs and we use a lookup table to be able to look up an LA from an OA. [More details here](https://www.rgs.org/geography/news/the-geographers-making-sense-of-census-2021/). So we aggregate the data to Local Authority (LA).


In [10]:
#Load the census data
census_data = pd.read_csv("data/2011_census_oa.csv")

#Merge with a lookup to LA
lookup = pd.read_csv("data/oa_la_lookup.csv")
census_data = pd.merge(census_data,lookup);

#sum the census data by LA
censusByLA = census_data.groupby('LOCAL_AUTHORITY_CODE').sum();
censusByLA

OA  \
LOCAL_AUTHORITY_CODE                                                      
E06000001             E00060255E00060256E00060257E00060258E00060259E...   
E06000002             E00060556E00060557E00060558E00060559E00060560E...   
E06000003             E00060999E00061000E00061001E00061002E00061003E...   
E06000004             E00061461E00061462E00061463E00061464E00061465E...   
E06000005             E00062043E00062044E00062045E00062046E00062047E...   
...                                                                 ...   
W06000020             W00007742W00007743W00007744W00007745W00007746W...   
W06000021             W00008044W00008045W00008046W00008047W00008048W...   
W06000022             W00008328W00008329W00008330W00008331W00008332W...   
W06000023             W00002268W00002269W00002270W00002271W00002272W...   
W06000024             W00006756W00006757W00006758W00006759W00006760W...   

                      Total_Population  Total_Households  \
LOCAL_AUTHORITY_CODE                                       
E06000001                        92028             40434   
E06000002                       138412             57203   
E06000003                       135177             59605   
E06000004                       191610             79159   
E06000005                       105564             46670   
...                                ...               ...   
W06000020                        91075             38524   
W06000021                        91323             38233   
W06000022                       145736             61172   
W06000023                       132976             58345   
W06000024                        58802             24264   

                      Total_Population_16_and_over  Total_Population_16_to_74  \
LOCAL_AUTHORITY_CODE                                                            
E06000001                                    74228                      66804   
E06000002                                   110409                     100551   
E06000003                                   111011                      99177   
E06000004                                   154503                     140654   
E06000005                                    85357                      76635   
...                                            ...                        ...   
W06000020                                    73833                      66107   
W06000021                                    75080                      66107   
W06000022                                   116348                     105141   
W06000023                                   110083                      96069   
W06000024                                    47842                      43377   

                      Total_Employment_16_to_74  \
LOCAL_AUTHORITY_CODE                              
E06000001                                 37767   
E06000002                                 54547   
E06000003                                 56354   
E06000004                                 87122   
E06000005                                 49014   
...                                         ...   
W06000020                                 40261   
W06000021                                 42817   
W06000022                                 64408   
W06000023                                 63653   
W06000024                                 25099   

                      Total_Population_in_Households_16_and_over  Age_0_to_4  \
LOCAL_AUTHORITY_CODE                                                           
E06000001                                                  73296        5698   
E06000002                                                 108161        9431   
E06000003                                                 109763        7553   
E06000004                                                 150859       12322   
E06000005                                                  83954        6579   
...                               

Most of the census variables give raw counts of people or households. Let's divide all the columns by the population to get proportions that account for the varying population sizes of different Local Authorities. (Note that this doesn't make sense for most columns - I've corrected POPULATION, but you might want to correct others, such as total_households).

In [11]:
import numpy as np
#just select the numerical columns
just_numerical=censusByLA.select_dtypes(include=np.number)

#divide numerical columns by population
censusByLA_normalised=just_numerical.div(censusByLA['POPULATION'],axis=0)

#correct population
censusByLA_normalised['POPULATION']=censusByLA['POPULATION']

censusByLA_normalised

Total_Population  Total_Households  \
LOCAL_AUTHORITY_CODE                                       
E06000001                          1.0          0.439366   
E06000002                          1.0          0.413281   
E06000003                          1.0          0.440940   
E06000004                          1.0          0.413126   
E06000005                          1.0          0.442101   
...                                ...               ...   
W06000020                          1.0          0.422992   
W06000021                          1.0          0.418657   
W06000022                          1.0          0.419745   
W06000023                          1.0          0.438763   
W06000024                          1.0          0.412639   

                      Total_Population_16_and_over  Total_Population_16_to_74  \
LOCAL_AUTHORITY_CODE                                                            
E06000001                                 0.806581                   0.725910   
E06000002                                 0.797684                   0.726462   
E06000003                                 0.821227                   0.733683   
E06000004                                 0.806341                   0.734064   
E06000005                                 0.808581                   0.725958   
...                                            ...                        ...   
W06000020                                 0.810684                   0.725852   
W06000021                                 0.822137                   0.723881   
W06000022                                 0.798348                   0.721448   
W06000023                                 0.827841                   0.722454   
W06000024                                 0.813612                   0.737679   

                      Total_Employment_16_to_74  \
LOCAL_AUTHORITY_CODE                              
E06000001                              0.410386   
E06000002                              0.394092   
E06000003                              0.416890   
E06000004                              0.454684   
E06000005                              0.464306   
...                                         ...   
W06000020                              0.442064   
W06000021                              0.468852   
W06000022                              0.441950   
W06000023                              0.478680   
W06000024                              0.426839   

                      Total_Population_in_Households_16_and_over  Age_0_to_4  \
LOCAL_AUTHORITY_CODE                                                           
E06000001                                               0.796453    0.061916   
E06000002                                               0.781442    0.068137   
E06000003                                               0.811995    0.055875   
E06000004                                               0.787323    0.064308   
E06000005                                               0.795290    0.062322   
...                                                          ...         ...   
W06000020                                               0.802866    0.059083   
W06000021                                               0.806150    0.050776   
W06000022                                               0.787232    0.065481   
W06000023                                               0.814643    0.049498   
W06000024                                               0.805738    0.061733   

                      Age_5_to_9  Age_10_to_14  Age_15_to_19  ...  \
LOCAL_AUTHORITY_CODE                                          ...   
E06000001               0.056418      0.061427      0.068218  ...   
E06000002               0.059793      0.061302      0.072710  ...   
E06000003               0.052509      0.057724      0.065359  ...   
E06000004               0.057267      0.059793      0.066902  ...   
E06000005               0.057539      0.058959      0.060703  ...   

Now let's merge these to the referendum data as a new dataframe `data`

In [12]:
data = pd.merge(referendum_data,censusByLA_normalised,left_on='Area_Code', right_on='LOCAL_AUTHORITY_CODE', how='inner')
data

geo_code                                           geometry  \
0    S12000028  POLYGON ((243296.000 588978.200, 242159.500 58...   
1    E07000011  POLYGON ((507472.314 299057.906, 511995.531 29...   
2    E07000083  POLYGON ((381509.283 230085.397, 385473.094 23...   
3    E07000127  POLYGON ((337708.438 420693.956, 337713.301 42...   
4    E06000005  POLYGON ((419709.307 515678.312, 418911.500 51...   
..         ...                                                ...   
373  E07000049  POLYGON ((395369.690 116934.897, 397676.807 11...   
374  E07000046  POLYGON ((245929.902 126948.298, 257377.496 12...   
375  E06000004  MULTIPOLYGON (((436387.995 522354.195, 440052....   
376  S12000024  POLYGON ((321168.000 718296.600, 319686.200 71...   
377  E07000169  MULTIPOLYGON (((452922.656 447657.846, 455350....   

        shapeArea Region_Code                    Region  Area_Code  \
0    1.220472e+09   S92000003                  Scotland  S12000028   
1    9.127571e+08   E12000006                      East  E07000011   
2    4.164018e+08   E12000009                South West  E07000083   
3    3.580191e+08   E12000002                North West  E07000127   
4    2.007936e+08   E12000001                North East  E06000005   
..            ...         ...                       ...        ...   
373  3.595242e+08   E12000009                South West  E07000049   
374  9.852863e+08   E12000009                South West  E07000046   
375  1.935023e+08   E12000001                North East  E06000004   
376  5.373173e+09   S92000003                  Scotland  S12000024   
377  6.024568e+08   E12000003  Yorkshire and The Humber  E07000169   

                  Area  Electorate  Turnout  Valid_Votes  ...  \
0       South Ayrshire       88116   0.6984        61506  ...   
1      Huntingdonshire      128486   0.7782        99927  ...   
2           Tewkesbury       67831   0.7915        53652  ...   
3      West Lancashire       85834   0.7447        63869  ...   
4           Darlington       77662   0.7107        55166  ...   
..                 ...         ...      ...          ...  ...   
373        East Dorset       71966   0.8133        58488  ...   
374           Torridge       52881   0.7841        41429  ...   
375   Stockton-on-Tees      141486   0.7100       100415  ...   
376  Perth and Kinross      110224   0.7375        81255  ...   
377              Selby       65278   0.7910        51603  ...   

     Associate_professional_and_technical_occupations  \
0                                            0.054433   
1                                            0.073277   
2                                            0.065802   
3                                            0.049410   
4                                            0.054384   
..                                                ...   
373                                          0.056731   
374                                          0.037751   
375                                          0.053912   
376                                          0.060906   
377                                          0.061451   

     Administrative_and_secretarial_occupations  Skilled_trades_occupations  \
0                                      0.047908                    0.058981   
1                                      0.063437                    0.060440   
2                                      0.072721                    0.060725   
3                                      0.052618                    0.054849   
4                                      0.055758                    0.055019   
..                                          ...                         ...   
373                                    0.057006                    0.061825   
374                                    0.040947                    0.099626   
375                                    0.051600                    0.052915   
376                                    0.049184                    0.069539   
3

In [13]:
data["pop_density"]= data["POPULATION"].div(data['shapeArea'],axis=0)
data["pop_density"]

0      0.000092
1      0.000186
2      0.000197
3      0.000309
4      0.000526
         ...   
373    0.000242
374    0.000065
375    0.000990
376    0.000027
377    0.000139
Name: pop_density, Length: 378, dtype: float64

### Task 2: Come up with some questions (analytical tasks) on helping explain the voting patterns.

Socioeconomic variables may help explain some of the behaviour. Come up with some questions (analytical tasks) on the referendum data. 

These may include:
 - which socioeconomic variables correlate to the voting patterns? 
 - which of these can help explain the patterns?
 
**Use whichever software and/or libraries you like!**

YOUR ANSWER HERE

### Examples for task 2

Use whichever software and/or libraries you like!

Pandas' `corr()` function calculate all pairwise correlations. We first extract only the numerical values. We only take correlations with our independent variable. We also calculate the absolute values and sort by these, but colour using a diverging colour scheme.

In [14]:
just_numerical=data.select_dtypes(include=np.number)
correlations_leave_remain=just_numerical.corr()[["leave_remain"]].reset_index()
#calculate absolute verions of each
correlations_leave_remain["abs_leave_remain"]=correlations_leave_remain["leave_remain"].abs()

alt.Chart(correlations_leave_remain).mark_bar(strokeWidth=0).encode(
    x='abs_leave_remain:Q',
    y=alt.Y('index:N',sort='-x'),
    color=alt.Color('leave_remain:Q', scale=alt.Scale(scheme='redblue',domain=([-1,1]))),
    tooltip=['index']
).properties(
    width=200,
    height=1000
)

alt.Chart(...)

In [15]:
alt.Chart(data).mark_circle(strokeWidth=0,opacity=0.3).encode(
    x='Leave:Q',
    y='pop_density:Q',
    color='Region',
    tooltip=['Area:N','Region']
).properties(
    width=200,
    height=200
)

alt.Chart(...)

In [16]:
alt.Chart(data).mark_geoshape(strokeWidth=1,stroke='lightgray',strokeOpacity=0.2
).encode(
    color=alt.Color('Very_good_health:Q', scale=alt.Scale(scheme='reds',domain=([0.3,0.7]))),
    tooltip=['Area:N','Very_good_health:Q','Region:N']
).properties(
 projection={'type': 'identity','reflectY': True},
    width=200,
    height=300
)

alt.Chart(...)

### Task 3: Come up with some interpretations

Can you interpret some of the issues behind the referendum outcome?

YOUR ANSWER HERE